<a href="https://colab.research.google.com/github/anqi-guo/duplicated_complaints_identification/blob/main/5_infer.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive')

raw_data_path = '/content/drive/My Drive/work/重复线索识别/data/raw_data'
stopwords_path = '/content/drive/My Drive/work/重复线索识别/data/stopwords'

import pandas as pd
orig_df = pd.read_csv(f'{raw_data_path}/raw_data.csv')

Mounted at /content/drive


/usr/local/lib/python3.7/dist-packages/IPython/core/interactiveshell.py:2882: DtypeWarning: Columns (1,2) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [2]:
!pip install hanlp[full]
!pip install sentence_transformers

     |████████████████████████████████| 576 kB 5.1 MB/s 
     |████████████████████████████████| 3.8 MB 61.9 MB/s 
     |████████████████████████████████| 46 kB 4.4 MB/s 
     |████████████████████████████████| 458.3 MB 10 kB/s 
     |████████████████████████████████| 43 kB 1.7 MB/s 
     |████████████████████████████████| 1.3 MB 64.6 MB/s 
     |████████████████████████████████| 4.5 MB 46.2 MB/s 
     |████████████████████████████████| 213 kB 72.1 MB/s 
     |████████████████████████████████| 132 kB 70.5 MB/s 
     |████████████████████████████████| 14.8 MB 50.8 MB/s 
     |████████████████████████████████| 42 kB 1.0 MB/s 
     |████████████████████████████████| 77 kB 6.3 MB/s 
     |████████████████████████████████| 895 kB 75.6 MB/s 
     |████████████████████████████████| 6.5 MB 57.2 MB/s 
     |████████████████████████████████| 596 kB 80.5 MB/s 
  Created wheel for clang: filename=clang-5.0-py3-none-any.whl size=30694 sha256=7222e7e673036722cc06674516d85992ff5d093de4b26e2b2a49f9311

     |████████████████████████████████| 79 kB 2.5 MB/s 
     |████████████████████████████████| 1.2 MB 6.2 MB/s 
  Created wheel for sentence-transformers: filename=sentence_transformers-2.2.0-py3-none-any.whl size=120747 sha256=4a5ba7e004715a3db0f9fdc6659ca2092a17f167ee6fb0614dd0fab273a28d8a
  Stored in directory: /root/.cache/pip/wheels/83/c0/df/b6873ab7aac3f2465aa9144b6b4c41c4391cfecc027c8b07e7
Successfully built sentence-transformers


In [3]:
import hanlp
tok = hanlp.load(hanlp.pretrained.tok.COARSE_ELECTRA_SMALL_ZH)
ner = hanlp.load(hanlp.pretrained.ner.MSRA_NER_ELECTRA_SMALL_ZH)

import regex as re
import jieba
import json

def extract_problem(text):
  # 删掉标点符号
  text = re.sub(r'\p{P}+', '', text) 
  # 删掉空格、换行符、信息保密、信息不保密、距离、时间、数字、投诉人信息
  text = re.sub(r'(\s|\n|信息[不]?保密|\d+[m米年月日]?|(.{1}先生|.{1}女士|市民)(来电)?反映)', '', text) 

  if '问题描述' in text and '诉求目的' in text:
    text = re.search(r'(?<=问题描述).*(?=诉求目的)', text).group()

  # 删掉停用词
  with open(f'{stopwords_path}/cn_stopwords.txt') as f:
    stopwords = f.read().splitlines() 

  seg_list = jieba.cut(text)

  result = ''.join([s for s in seg_list if s not in stopwords])
  return result

def extract_location(sentence):
    nerred_sent = ner(tok(sentence))
    # 提取命名实体是ORGANIZATION或者LOCATION，且结尾不是市镇区县的词
    locations = [l[0] for l in nerred_sent if (l[1]=='ORGANIZATION' or l[1]=='LOCATION') and len(re.findall('[市镇区县]$', l[0]))==0]

    return locations

def extract_loupan(text):
  loupan_list = []
  address_list = []

  with open(f'{raw_data_path}/新楼盘.json') as json_file:
    loupan = json.load(json_file)

  with open(f'{raw_data_path}/旧楼盘.json') as json_file:
    old_loupan = json.load(json_file)

  loupan.update(old_loupan)

  for lp, addr in loupan.items():
    if lp in text:
      loupan_list.append(lp)
      address_list.append(addr)

  address_list = [item for sublist in address_list for item in sublist]

  return loupan_list, address_list

def extract_address(text):
  location_list = extract_location(text)
  loupan_list, loupan_address_list = extract_loupan(text)

  address_list = location_list + loupan_list + loupan_address_list
  address_list = [l for l in address_list if len(l)>2]
  
  return set(address_list)

100%  43.5 MiB   5.0 MiB/s ETA:  0 s [=========================================]
Decompressing /root/.hanlp/tok/coarse_electra_small_20220220_013548.zip to /root/.hanlp/tok
100%  26.7 KiB  26.7 KiB/s ETA:  0 s [=========================================]
Decompressing /root/.hanlp/utils/char_table_20210602_202632.json.zip to /root/.hanlp/utils
100%  41.2 KiB  41.2 KiB/s ETA:  0 s [=========================================]
Decompressing /root/.hanlp/transformers/electra_zh_small_20210706_125427.zip to /root/.hanlp/transformers
100%  45.0 MiB   6.0 MiB/s ETA:  0 s [=========================================]
Decompressing /root/.hanlp/ner/msra_ner_electra_small_20220215_205503.zip to /root/.hanlp/ner


In [4]:
df = orig_df[~orig_df['XSNR'].str.contains('前期工单|原工单|已有工单|前单号|类似工单')]
df.shape

(71717, 16)

In [5]:
from tqdm.auto import tqdm
tqdm.pandas()

df['problem'] = df['XSNR'].progress_apply(extract_problem)

  0%|          | 0/71717 [00:00<?, ?it/s]

Building prefix dict from the default dictionary ...
Dumping model to file cache /tmp/jieba.cache
Loading model cost 1.006 seconds.
Prefix dict has been built successfully.
/usr/local/lib/python3.7/dist-packages/ipykernel_launcher.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  after removing the cwd from sys.path.


In [8]:
from collections import defaultdict
from sentence_transformers import SentenceTransformer, util
model = SentenceTransformer('/content/drive/My Drive/work/重复线索识别/models/sb')

def get_similar_sentences(df):
  dict_ = defaultdict(list)
  df['address_list'] = df['problem'].progress_apply(extract_address)

  for idx1, row1 in tqdm(df.iterrows(), desc='get_similar_sentence', total=len(df)):
    for idx2, row2 in df.iterrows():
      if idx1!=idx2:
        intersection = list(row1['address_list'].intersection(row2['address_list']))
        if len(intersection) > 0:
          intersection.sort()
          if idx1 not in dict_[','.join(intersection)]:
            dict_[','.join(intersection)].append(idx1)
          if idx2 not in dict_[','.join(intersection)]:
            dict_[','.join(intersection)].append(idx2)

  return dict_


def get_top_similar_sentences(model, df, similar_sentences_index_list, top_k=10):
  similar_sentences_list = df.loc[similar_sentences_index_list, 'problem'].tolist()
  paraphrases = util.paraphrase_mining(model, similar_sentences_list, show_progress_bar=False, max_pairs=20, top_k=top_k)

  similar_sentences_pairs = []
  for paraphrase in paraphrases:
      score, i, j = paraphrase
      if i != j and score > .7 and score < 1:
          #print(df.loc[similar_sentences_index_list[i],'XSNR'],'|', df.loc[similar_sentences_index_list[j], 'XSNR'])
          df_s = pd.DataFrame(data={
              'score':[score], 
              'sentence1':[df.loc[similar_sentences_index_list[i],'XSNR']], 
              'sentence2':[df.loc[similar_sentences_index_list[j], 'XSNR']], 
              'bh1': [df.loc[similar_sentences_index_list[i], 'BH']], 
              'bh2': [df.loc[similar_sentences_index_list[j], 'BH']]})
          df_s.to_csv(f'/content/drive/My Drive/work/重复线索识别/data/model_outputs/similar_sentence_pairs.csv', mode='a', header=False, index=False)


In [ ]:
from collections import OrderedDict
xzqh_cnt = {}

for i in df['XZQH'].unique():
  xzqh_cnt[i] = len(df[df['XZQH']==i])

xzqh_cnt = OrderedDict(sorted(xzqh_cnt.items(), key = lambda x: x[1], reverse = False))

for i in list(xzqh_cnt.items())[1:]:
    print(i)
    df_i = df[df['XZQH']==i[0]].reset_index(drop=True)
    dict_ = get_similar_sentences(df_i)

    for k,v in tqdm(dict(dict_).items(), desc=k):
        get_top_similar_sentences(model, df_i, v)

('宝应湖农场', 5)


  0%|          | 0/5 [00:00<?, ?it/s]

get_similar_sentence:   0%|          | 0/5 [00:00<?, ?it/s]

朝阳路: 0it [00:00, ?it/s]

('清江浦区淮安现代商务集聚区管委会', 18)


...

水利局,高良涧街道:   0%|          | 0/770 [00:00<?, ?it/s]

('经济技术开发区', 4261)


  0%|          | 0/4261 [00:00<?, ?it/s]

get_similar_sentence:   0%|          | 0/4261 [00:00<?, ?it/s]

淮村村四组:   0%|          | 0/1197 [00:00<?, ?it/s]

In [ ]:
data = pd.read_csv(f'/content/drive/My Drive/work/重复线索识别/data/model_outputs/similar_sentence_pairs.csv', header=None)
data.columns = ['相似度','线索内容1','线索内容2','编号1','编号2']
print(len(data))
data.drop_duplicates(subset=['线索内容1','线索内容2'], inplace=True)
print(len(data))
data.to_excel(f'/content/drive/My Drive/work/重复线索识别/data/model_outputs/similar_sentence_pairs.xlsx', index=False)

In [ ]:
# load fine-tuned model
'''
from sentence_transformers import SentenceTransformer, util
model = SentenceTransformer('/content/drive/My Drive/work/重复线索识别/models/sb')

for i in df['XZQH'].unique():
    print(i)
    df_i = df[df['XZQH']==i].reset_index(drop=True)
    sentences = df_i['problem'].tolist()
    paraphrases = util.paraphrase_mining(model, sentences, show_progress_bar=True, max_pairs=5000, top_k=10)

    similar_sentence_pairs = []
    for paraphrase in paraphrases:
        score, i, j = paraphrase
        if i != j and score > .8 and score < 1:
            df_s = pd.DataFrame(data={'score':[score], 'sentence1':[df_i.loc[i,'XSNR']], 'sentence2':[df_i.loc[j, 'XSNR']], 'bh1': [df_i.loc[i, 'BH']], 'bh2': [df_i.loc[j, 'BH']]})
            df_s.to_csv(f'/content/drive/My Drive/work/重复线索识别/data/model_outputs/similar_sentence_pairs.csv', mode='a', header=False, index=False)
'''